In [2]:
# Notebooks
import nbimporter
import os
import sys

# Functions from src
module_path = os.path.abspath(os.path.join('..'))
if module_path not in sys.path:
    sys.path.append(module_path)
    
# Defined Functions
from utils import *

# Pandas, matplotlib, pickle, seaborn
import pickle
import numpy as np
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt

from statistics import mean
from collections import Counter
from tgan.model import TGANModel

random_state = 13


/home/matias/anaconda3/envs/tgan/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:516: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
/home/matias/anaconda3/envs/tgan/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:517: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
/home/matias/anaconda3/envs/tgan/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:518: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
/home/matias/anaconda3/envs/tgan/lib/python3.7/site-

/home/matias/anaconda3/envs/tgan/lib/python3.7/site-packages/tensorboard/compat/tensorflow_stub/dtypes.py:541: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
/home/matias/anaconda3/envs/tgan/lib/python3.7/site-packages/tensorboard/compat/tensorflow_stub/dtypes.py:542: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
/home/matias/anaconda3/envs/tgan/lib/python3.7/site-packages/tensorboard/compat/tensorflow_stub/dtypes.py:543: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
/home/matias/anaconda3/envs/tga

In [3]:
# global variables/constants
num_trials = 30
test_size_percentage = 0.2 # for CV within train split
fixed_depth = 10


# Load Datasets

## Occutherm

In [4]:
df_tcs_train = pd.read_pickle("data/occutherm/df_feature1_train.pkl") 
df_tcs_test = pd.read_pickle("data/occutherm/df_feature1_test.pkl")

# total count for instances per class: 818
print(df_tcs_train.info())


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1508 entries, 0 to 1507
Data columns (total 10 columns):
Temperature (Fahrenheit)       1508 non-null float64
SkinTemperature                1508 non-null float64
ClothingInsulation             1508 non-null float64
Height(cm)                     1508 non-null float64
Shoulder Circumference(cm)     1508 non-null float64
Weight(lbs)                    1508 non-null float64
Gender                         1508 non-null int64
Temperature_outside            1508 non-null float64
Humidity_outside               1508 non-null float64
Discrete Thermal Comfort_TA    1508 non-null int64
dtypes: float64(8), int64(2)
memory usage: 117.9 KB
None


## Cresh

In [5]:
df_cresh_train = pd.read_pickle("data/cresh/cresh_train.pkl")
df_cresh_test = pd.read_pickle("data/cresh/cresh_test.pkl")

# total count for instances per class: 713
print(df_cresh_train.info())


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1159 entries, 0 to 1158
Data columns (total 11 columns):
heartRate_cozie        1159 non-null float64
humidity_sensing       1159 non-null float64
light_sensing          1159 non-null float64
noise_sensing          1159 non-null float64
temperature_sensing    1159 non-null float64
temperature_mbient     1159 non-null float64
hour_sin               1159 non-null float64
hour_cos               1159 non-null float64
day_of_week_sin        1159 non-null float64
day_of_week_cos        1159 non-null float64
thermal_cozie          1159 non-null int64
dtypes: float64(10), int64(1)
memory usage: 99.7 KB
None


## ASHRAE

In [6]:
df_ashrae_train = pd.read_pickle("data/ashrae/ashrae_train.pkl")
df_ashrae_test = pd.read_pickle("data/ashrae/ashrae_test.pkl")

print(df_ashrae_train.info())


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 46477 entries, 0 to 46476
Data columns (total 7 columns):
SET                          46477 non-null float64
Clo                          46477 non-null float64
Met                          46477 non-null float64
Air temperature (¡C)         46477 non-null float64
Relative humidity (%)        46477 non-null float64
Air velocity (m/s)           46477 non-null float64
Thermal sensation rounded    46477 non-null float64
dtypes: float64(7)
memory usage: 2.5 MB
None


# Samplig synthetic datasets

https://sdv-dev.github.io/TGAN/

Update the `config.json` file according to the `TGAN` documentation and run `tgan_hyperparameters.sh` to find the best set of hyper-parameters for the model. 

Use these hyper-parameters in `train_tgan_<dataset>.sh` to train the model.

The generation and evaluation of generated samples is done in the next cells.


## Occutherm
Required samples

| Model | -2 | -1 | 0 | 1 | 2 |
|---|---|---|---|---|---|
| SMOTE | 646 | 515 | 0 | 647 | 774 |
| ADASYN | 651 | 519 | 0 | 680 | 770 |


## Cresh
Required samples

| Model | 9 | 10 | 11 |
|---|---|---|---|
| SMOTE | 547 | 0 | 433 |
| ADASYN | 534 | 0 | 402 |


## ASHRAE
Required samples

| Model  | -3 | -2 | -1 | 0 | 1 | 2 | 3 |
|--------|----|----|----|---|---|---|---|
| SMOTE  | 17894 | 16287 | 11695 | 0 | 10161 | 14096 | 16173 |
| ADASYN | 18159 | 16619 | 12065 | 0 | 10987 | 14974 | 16971 |


# TGAN


In [7]:
def sample_TGAN(df, dataset="occutherm", logs=False):
    # load require samples to balance and initial count
    if dataset == "occutherm":
        # samples to generate per label
        occutherm_req_two = 774
        occutherm_req_one = 647
        occutherm_req_zero = 0 
        occutherm_req_minus_one = 515
        occutherm_req_minus_two = 646
        # count of generated samples per label
        count_two = 0
        count_one = 0
        count_minus_one = 0
        count_minus_two = 0 
    elif dataset == "cresh":
        # samples to generate per label
        cresh_req_eleven = 433
        cresh_req_ten = 0
        cresh_req_nine = 547
        # count of generated samples per label
        count_nine = 0
        count_eleven = 0
    elif dataset == "ashrae":
        # samples to generate per label
        ashrae_req_three = 16173
        ashrae_req_two = 14096
        ashrae_req_one = 10161 
        ashrae_req_zero = 0
        ashrae_req_minus_one = 11695
        ashrae_req_minus_two = 16287
        ashrae_req_minus_three = 17894
        # count of generated samples per label
        count_three = 0
        count_two = 0
        count_one = 0
        count_minus_one = 0
        count_minus_two = 0
        count_minus_three = 0

    samples_count = 0 # total number of samples generated
    finish_loop = False
    
    # samples to generated every loop
    if dataset == "ashrae":
        print_threshold = 10000
    else:
        print_threshold = 1000 # previous 1k

    # initiliaze synthetic dataframe
    columns = df.columns.values
    df_synth = pd.DataFrame(columns=columns)
    
    # load model
    model_path = "models/tgan_" + dataset + ".pkl"
    tgan = TGANModel.load(model_path)

    while True:
        if finish_loop:
            samples_count += print_threshold
            break
        
        # generate `print_threshold` samples
        curr_df = tgan.sample(print_threshold)
        
        # classes generated
        print(curr_df.iloc[:, -1].unique()) # DEBUG
        
        # iterate through the generated samples
        if dataset == "occutherm":
            for index, row in curr_df.iterrows():  
                if (row['Discrete Thermal Comfort_TA'] == '2') and (count_two != occutherm_req_two): 
                    df_synth = df_synth.append(row)
                    count_two += 1 
                elif (row['Discrete Thermal Comfort_TA'] == '1') and (count_one != occutherm_req_one): 
                    df_synth = df_synth.append(row)
                    count_one += 1
                elif (row['Discrete Thermal Comfort_TA'] == '-1') and (count_minus_one != occutherm_req_minus_one): 
                    df_synth = df_synth.append(row)
                    count_minus_one += 1
                elif (row['Discrete Thermal Comfort_TA'] == '-2') and (count_minus_two != occutherm_req_minus_two): 
                    df_synth = df_synth.append(row)
                    count_minus_two += 1
                elif (count_two == occutherm_req_two) and \
                    (count_one == occutherm_req_one) and \
                    (count_minus_one == occutherm_req_minus_one) and \
                    (count_minus_two == occutherm_req_minus_two):
                    finish_loop = True
                    break
                  
        elif dataset == "cresh":
            for index, row in curr_df.iterrows():  
                if (row['thermal_cozie'] == '9') and (count_nine != cresh_req_nine): 
                    df_synth = df_synth.append(row)
                    count_nine += 1 
                elif (row['thermal_cozie'] == '11') and (count_eleven != cresh_req_eleven): 
                    df_synth = df_synth.append(row)
                    count_eleven += 1
                elif (count_nine == cresh_req_nine) and \
                    (count_eleven == cresh_req_eleven):
                    finish_loop = True
                    break

        elif dataset == "ashrae":
            for index, row in curr_df.iterrows(): 
                if (row['Thermal sensation rounded'] == '3.0') and (count_three != ashrae_req_three): 
                    df_synth = df_synth.append(row)
                    count_three += 1 
                elif (row['Thermal sensation rounded'] == '2.0') and (count_two != ashrae_req_two): 
                    df_synth = df_synth.append(row)
                    count_two += 1
                elif (row['Thermal sensation rounded'] == '1.0') and (count_one != ashrae_req_one): 
                    df_synth = df_synth.append(row)
                    count_one += 1
                elif (row['Thermal sensation rounded'] == '-1.0') and (count_minus_one != ashrae_req_minus_one): 
                    df_synth = df_synth.append(row)
                    count_minus_one += 1
                elif (row['Thermal sensation rounded'] == '-2.0') and (count_minus_two != ashrae_req_minus_two): 
                    df_synth = df_synth.append(row)
                    count_minus_two += 1
                elif (row['Thermal sensation rounded'] == '-3.0') and (count_minus_three != ashrae_req_minus_three): 
                    df_synth = df_synth.append(row)
                    count_minus_three += 1
                elif (count_three == ashrae_req_three) and \
                     (count_two == ashrae_req_two) and \
                     (count_one == ashrae_req_one) and \
                     (count_minus_one == ashrae_req_minus_one) and \
                     (count_minus_two == ashrae_req_minus_two) and \
                     (count_minus_three == ashrae_req_minus_three):
                    finish_loop = True
                    break

        samples_count += print_threshold

    if logs:
        print('Original {} train dataset shape {}'.format(df, Counter(y)))        
        print('Resampled (TGAN) synth dataset shape %s' % Counter(np.array(df_synth.iloc[:, -1])))

    if dataset == "occutherm":
        df_synth['Gender'] = pd.to_numeric(df_synth['Gender'], errors='coerce')
    # last column in float instead of string
    df_synth.iloc[:, -1] = pd.to_numeric(df_synth.iloc[:, -1], errors='coerce')

    return df_synth


In [8]:
def evaluate_on_dataset(df_train, df_test, dataset='occutherm'):
    model = 'tgan'
    # empty list to hold values during trials  
    variability_list = []
    diversity_list = []

    class_acc_test_list_0 = []
    class_acc_test_list_1 = []
    class_acc_test_list_2 = []
    class_acc_test_list_3 = []
    
    class_report_rdf_list = []

    for i in range(0, num_trials):      
        ###################################
        # Sample synthethic dataset for 'dataset'
        df_synth = sample_TGAN(df_train, dataset) # complement needed for balancing dataset        
        # merge synthethic + real dataset
        df_real_synth = pd.concat([df_synth, df_train])
        
        ###################################
        # Variability of generated samples
        variability = evaluation_variability(df_synth)
        variability_list.append(variability)
    
        #################################################
        # Class diversity with respect to the training set
        diversity = evaluation_diversity(df_synth, df_train, baseline=False)
        diversity_list.append(diversity)

        #####################################
        # Quality on the final classification
        # use best models NB, KNN, SVM, RDF
        class_acc_test, class_acc_train, class_models, class_report_rdf = evaluation_classification(df_real_synth, df_test, rdf_depth=fixed_depth, depth_file_name='default', test_size_percentage=test_size_percentage)
        class_acc_test_list_0.append(class_acc_test[0])
        class_acc_test_list_1.append(class_acc_test[1])
        class_acc_test_list_2.append(class_acc_test[2])
        class_acc_test_list_3.append(class_acc_test[3])
        class_report_rdf_list.append(class_report_rdf)
        
        ########################
        # end of for loop trials
        print("End of {} trial".format(i + 1))
        
    # get average of trials
    variability = mean(variability_list)
    diversity = mean(diversity_list)
    class_acc_test = [mean(class_acc_test_list_0), mean(class_acc_test_list_1), mean(class_acc_test_list_2), mean(class_acc_test_list_3)]
    
    #####################################
    # Saving results
    # Format is folder/<dataset_string>-<experiment_name>_<metric or model>_<test or train>_<model>.pkl
    save_pickle(variability, "metrics/" + dataset + "_variability_" + model + "_trials.pkl")
    save_pickle(diversity, "metrics/" + dataset + "_diversity_" + model + "_trials.pkl")
    save_pickle(class_acc_test, "metrics/" + dataset + "_classification_" + model + "_trials.pkl")
    save_pickle(class_report_rdf_list, "label-metrics/" + dataset + "_class_report_" + model + "_trials.pkl")

    print("################################################################################")
    print("# Metrics and models for dataset {} saved!".format(dataset))
    print("################################################################################")


### Occutherm

In [12]:
evaluate_on_dataset(df_tcs_train, df_tcs_test, dataset='occutherm')


[0708 19:54:37 @collection.py:146] New collections created in tower : tf.GraphKeys.REGULARIZATION_LOSSES
[0708 19:54:37 @collection.py:165] These collections were modified but restored in : (tf.GraphKeys.SUMMARIES: 0->2)
[0708 19:54:37 @sessinit.py:87] WRN The following variables are in the checkpoint, but not found in the graph: global_step, optimize/beta1_power, optimize/beta2_power
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
[0708 19:54:39 @sessinit.py:114] Restoring checkpoint from output/model/model-50000 ...
INFO:tensorflow:Restoring parameters from output/model/model-50000


  2%|2         |4/200[00:00<00:22, 8.54it/s]


['0' '-1' '1' '-2' '2']


  2%|2         |4/200[00:00<00:04,46.19it/s]


['-1' '0' '2' '1' '-2']


...

['0' '-2' '1' '-1' '2']


  2%|2         |4/200[00:00<00:04,42.60it/s]


['-2' '0' '-1' '1' '2']


  2%|2         |4/200[00:00<00:04,43.60it/s]


['-1' '-2' '0' '1' '2']
End of 30 trial
################################################################################
# Metrics and models for dataset occutherm saved!
################################################################################


### Cresh

In [13]:
evaluate_on_dataset(df_cresh_train, df_cresh_test, dataset='cresh')


[0708 20:13:51 @registry.py:126] gen/LSTM/13/FC3 input: [200, 5]
[0708 20:13:51 @registry.py:134] gen/LSTM/13/FC3 output: [200, 600]
[0708 20:13:51 @registry.py:126] gen/LSTM/15/FC3 input: [200, 5]
[0708 20:13:51 @registry.py:134] gen/LSTM/15/FC3 output: [200, 600]
[0708 20:13:52 @registry.py:126] gen/LSTM/18/FC input: [200, 400]
[0708 20:13:52 @registry.py:134] gen/LSTM/18/FC output: [200, 600]
[0708 20:13:52 @registry.py:126] gen/LSTM/18/FC2 input: [200, 600]
[0708 20:13:52 @registry.py:134] gen/LSTM/18/FC2 output: [200, 1]
[0708 20:13:52 @registry.py:126] gen/LSTM/19/FC input: [200, 400]
[0708 20:13:53 @registry.py:134] gen/LSTM/19/FC output: [200, 600]
[0708 20:13:53 @registry.py:126] gen/LSTM/19/FC2 input: [200, 600]
[0708 20:13:53 @registry.py:134] gen/LSTM/19/FC2 output: [200, 5]
[0708 20:13:53 @registry.py:126] gen/LSTM/19/FC3 input: [200, 5]
[0708 20:13:53 @registry.py:134] gen/LSTM/19/FC3 output: [200, 600]
[0708 20:13:53 @registry.py:126] gen/LSTM/20/FC input: [200, 400]
[07

  2%|2         |4/200[00:00<00:26, 7.48it/s]


['10' '11' '9']


  2%|2         |4/200[00:00<00:05,37.85it/s]


['10' '11' '9']


...

['10' '11' '9']


  2%|2         |4/200[00:00<00:04,44.27it/s]


['11' '10' '9']


  2%|2         |4/200[00:00<00:04,44.55it/s]


['10' '11' '9']
End of 30 trial
################################################################################
# Metrics and models for dataset cresh saved!
################################################################################


## ASHRAE


In [9]:
evaluate_on_dataset(df_ashrae_train, df_ashrae_test, dataset='ashrae')









Instructions for updating:
This class is equivalent as tf.keras.layers.LSTMCell, and will be replaced by that in Tensorflow 2.0.
Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor
Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor
[0710 00:06:10 @registry.py:126] gen/LSTM/00/FC input: [200, 400]

[0710 00:06:10 @registry.py:134] gen/LSTM/00/FC output: [200, 200]
[0710 00:06:10 @registry.py:126] gen/LSTM/00/FC2 input: [200, 200]
[0710 00:06:10 @registry.py:134] gen/LSTM/00/FC2 output: [200, 1]
[0710 00:06:10 @registry.py:126] gen/LSTM/01/FC input: [200, 400]
[0710 00:06:10 @registry.py:134] gen/LSTM/01/FC output: [200, 200]
[0710 00:06:10 @registry.py:126] gen/LSTM/01/FC2 input: [200, 200]
[0710 00:06:10 @registry.py:134] gen/LSTM/01/FC2 output: [200, 5]
[0710 00:06:10 @registry.py:126] gen/LSTM/01/FC3 input: [200, 5]
[0710 00:06:10 @registry.py:13

 24%|##4       |49/200[00:00<00:02,59.73it/s]


['-3.0' '0.0' '-0.0' '-2.0' '2.0' '3.0' '-1.0' '1.0']


 24%|##4       |49/200[00:00<00:01,127.03it/s]


['1.0' '0.0' '-2.0' '3.0' '-1.0' '-0.0' '2.0' '-3.0']


...

['2.0' '0.0' '1.0' '-2.0' '3.0' '-0.0' '-1.0' '-3.0']


 24%|##4       |49/200[00:00<00:01,116.56it/s]


['0.0' '-2.0' '1.0' '3.0' '2.0' '-1.0' '-3.0' '-0.0']


 24%|##4       |49/200[00:00<00:01,123.55it/s]


['0.0' '2.0' '3.0' '-1.0' '1.0' '-2.0' '-3.0' '-0.0']
End of 30 trial
################################################################################
# Metrics and models for dataset ashrae saved!
################################################################################
